In [17]:
import os
import torch
import torch.nn as nn
from PIL import Image
import numpy as np
from torchvision import transforms

# === Paths ===
base_image_folder = r'C:/Users/Manhab Zafar/Desktop/DIP-Project/yolov5/dataset/images'
base_label_folder = r'C:/Users/Manhab Zafar/Desktop/DIP-Project/yolov5/dataset/labels'

# Ensure base label directory exists
print(f"Creating base labels directory: {base_label_folder}")
os.makedirs(base_label_folder, exist_ok=True)

# === Class Labels (order matters) ===
classes = ['Avocado', 'Brocolli', 'Cabbage', 'Cantaloupe', 'Capsicum',
           'Cauliflower', 'Cucumber', 'Dates', 'Fig', 'Ginger',
           'Lemon', 'Lychee', 'Peach', 'Pear', 'Potato', 'Tomato',
           'apples', 'banana', 'blackberry', 'orange']

# === Define the same CNN model architecture used during training ===
class CNNModel(nn.Module):
    def __init__(self, num_classes=20):
        super(CNNModel, self).__init__()
        self.model = nn.Sequential(
            nn.Conv2d(3, 32, 3, padding=1), nn.ReLU(), nn.MaxPool2d(2),
            nn.Conv2d(32, 64, 3, padding=1), nn.ReLU(), nn.MaxPool2d(2),
            nn.Conv2d(64, 128, 3, padding=1), nn.ReLU(), nn.MaxPool2d(2),
            nn.Flatten(),
            nn.Linear(128 * 16 * 16, 256),
            nn.ReLU(),
            nn.Dropout(0.5),
            nn.Linear(256, num_classes)
        )

    def forward(self, x):
        return self.model(x)

# === Load the trained model ===
print("Loading model...")
try:
    model = CNNModel()
    model.load_state_dict(torch.load("fruit_veg_model.pth", map_location=torch.device('cpu')))
    model.eval()  # Set the model to evaluation mode
    print("Model loaded successfully!")
except Exception as e:
    print(f"Error loading model: {e}")
    exit(1)

# === Image transform (match training settings) ===
transform = transforms.Compose([
    transforms.Resize((128, 128)),  # Using 128x128 as in training
    transforms.ToTensor(),
    transforms.Normalize([0.5], [0.5])  # Same normalization as training
])

# === YOLO format conversion ===
def convert_to_yolo(x, y, w, h, img_w, img_h):
    x_center = (x + w / 2) / img_w
    y_center = (y + h / 2) / img_h
    return x_center, y_center, w / img_w, h / img_h

# === Process image function ===
def process_image(img_path, label_path, class_id=None):
    """Process a single image and create a label file"""
    try:
        image = Image.open(img_path).convert('RGB')
        print(f"  - Image opened successfully: {image.size}")
        np_img = np.array(image)
        gray = np.mean(np_img, axis=2).astype(np.uint8)

        # Simple threshold to separate foreground (fruits/veggies) from background
        threshold = 100
        mask = gray < threshold

        # Find bounding boxes manually
        objects = []
        visited = np.zeros_like(mask, dtype=bool)
        h, w = mask.shape

        def bfs(i, j):
            queue = [(i, j)]
            visited[i, j] = True
            coords = [(i, j)]
            while queue:
                ci, cj = queue.pop(0)
                for ni in range(max(0, ci-1), min(h, ci+2)):
                    for nj in range(max(0, cj-1), min(w, cj+2)):
                        if mask[ni, nj] and not visited[ni, nj]:
                            visited[ni, nj] = True
                            queue.append((ni, nj))
                            coords.append((ni, nj))
            return coords

        object_count = 0
        for i in range(h):
            for j in range(w):
                if mask[i, j] and not visited[i, j]:
                    coords = bfs(i, j)
                    if len(coords) > 0:  # Make sure coords is not empty
                        ys, xs = zip(*coords)
                        min_x, max_x = min(xs), max(xs)
                        min_y, max_y = min(ys), max(ys)
                        if (max_x - min_x > 30) and (max_y - min_y > 30):  # ignore small regions
                            objects.append((min_x, min_y, max_x - min_x, max_y - min_y))
                            object_count += 1

        print(f"  - Found {object_count} objects")
            
        # Ensure the label directory exists
        os.makedirs(os.path.dirname(label_path), exist_ok=True)
        
        # Write labels
        with open(label_path, 'w') as f:
            print(f"  - Writing to {label_path}")
            written_objects = 0
            for (x, y, box_w, box_h) in objects:
                try:
                    # If class_id is provided (from folder name), use it
                    # Otherwise predict with the model
                    if class_id is not None:
                        detected_class_id = class_id
                    else:
                        crop = image.crop((x, y, x + box_w, y + box_h))
                        input_tensor = transform(crop).unsqueeze(0)  # Add batch dimension
                        
                        with torch.no_grad():
                            output = model(input_tensor)
                            _, predicted = torch.max(output, 1)
                            detected_class_id = predicted.item()
                        
                    x_center, y_center, w_rel, h_rel = convert_to_yolo(x, y, box_w, box_h, w, h)
                    label_line = f"{detected_class_id} {x_center:.6f} {y_center:.6f} {w_rel:.6f} {h_rel:.6f}"
                    f.write(label_line + "\n")
                    written_objects += 1
                    
                except Exception as e:
                    print(f"  - Error processing object: {e}")
                    continue
            
            print(f"  - Wrote {written_objects} objects to label file")
        
        return True
    except Exception as e:
        print(f"Error processing image {img_path}: {e}")
        return False

# Check if base image folder exists
print(f"Looking for image folders in: {base_image_folder}")
if not os.path.exists(base_image_folder):
    print(f"ERROR: Base image folder does not exist: {base_image_folder}")
    exit(1)

# Find all first-level subfolders (test, train, validation)
dataset_splits = [f for f in os.listdir(base_image_folder) 
                 if os.path.isdir(os.path.join(base_image_folder, f))]

if not dataset_splits:
    print(f"ERROR: No dataset split folders found in {base_image_folder}")
    exit(1)

print(f"Found dataset splits: {dataset_splits}")

# Process all folders and subfolders
total_images_found = 0
total_images_processed = 0

for split in dataset_splits:
    split_path = os.path.join(base_image_folder, split)
    split_label_path = os.path.join(base_label_folder, split)
    
    # Create label directory for this split
    os.makedirs(split_label_path, exist_ok=True)
    print(f"\nProcessing {split} split...")
    
    # Find all class folders within this split
    class_folders = [f for f in os.listdir(split_path) 
                    if os.path.isdir(os.path.join(split_path, f))]
    
    print(f"Found {len(class_folders)} class folders in {split}")
    
    split_images_found = 0
    split_images_processed = 0
    
    for class_folder in class_folders:
        class_path = os.path.join(split_path, class_folder)
        class_label_path = os.path.join(split_label_path, class_folder)
        
        # Create label directory for this class
        os.makedirs(class_label_path, exist_ok=True)
        
        # Try to find class_id from the folder name
        try:
            class_id = classes.index(class_folder)
            print(f"\nProcessing class: {class_folder} (ID: {class_id})...")
        except ValueError:
            print(f"\nWARNING: Class name '{class_folder}' not found in classes list. Will use model prediction.")
            class_id = None
        
        # Get all image files in this class folder
        image_files = [f for f in os.listdir(class_path) 
                      if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
        
        print(f"Found {len(image_files)} images in {class_folder}")
        split_images_found += len(image_files)
        class_processed = 0
        
        # Process each image
        for img_file in image_files:
            img_path = os.path.join(class_path, img_file)
            label_path = os.path.join(class_label_path, os.path.splitext(img_file)[0] + '.txt')
            
            print(f"Processing {split}/{class_folder}/{img_file}...")
            success = process_image(img_path, label_path, class_id)
            
            if success:
                class_processed += 1
                split_images_processed += 1
                print(f"[✔] Labeled: {split}/{class_folder}/{img_file}")
        
        print(f"Processed {class_processed}/{len(image_files)} images in {class_folder}")
    
    total_images_found += split_images_found
    total_images_processed += split_images_processed
    print(f"\n=== {split} Summary ===")
    print(f"Found: {split_images_found} images")
    print(f"Processed: {split_images_processed} images")

print(f"\n=== OVERALL SUMMARY ===")
print(f"Total images found: {total_images_found}")
print(f"Total images processed: {total_images_processed}")
print(f"Label files should be in: {base_label_folder}")
print(f"Processing complete!")

Creating base labels directory: C:/Users/Manhab Zafar/Desktop/DIP-Project/yolov5/dataset/labels
Loading model...
Model loaded successfully!
Looking for image folders in: C:/Users/Manhab Zafar/Desktop/DIP-Project/yolov5/dataset/images
Found dataset splits: ['test', 'train', 'val']

Processing test split...
Found 20 class folders in test

Processing class: apples (ID: 16)...
Found 187 images in apples
Processing test/apples/100_100.jpg...
  - Image opened successfully: (100, 100)
  - Found 1 objects
  - Writing to C:/Users/Manhab Zafar/Desktop/DIP-Project/yolov5/dataset/labels\test\apples\100_100.txt
  - Wrote 1 objects to label file
[✔] Labeled: test/apples/100_100.jpg
Processing test/apples/113_100.jpg...
  - Image opened successfully: (100, 100)
  - Found 1 objects
  - Writing to C:/Users/Manhab Zafar/Desktop/DIP-Project/yolov5/dataset/labels\test\apples\113_100.txt
  - Wrote 1 objects to label file
[✔] Labeled: test/apples/113_100.jpg
Processing test/apples/120_100.jpg...
  - Image o